In [1]:
import sys

In [2]:
# Install PyAthena
!{sys.executable} -m pip install -q --upgrade pip
!{sys.executable} -m pip install -q PyAthena
!{sys.executable} -m pip install -q awswrangler
!{sys.executable} -m pip install -q pymysql


In [61]:
#!/usr/bin/env python
# -*- coding: utf-8 -*-

import pandas as pd
import datetime
import numpy as np
import pymysql
import boto3
import awswrangler as wr

### connection info
rds_host_write  = "database-ambt.cluster-cvnwxgmngsms.ap-northeast-2.rds.amazonaws.com"
rds_host_read  = "database-ambt.cluster-ro-cvnwxgmngsms.ap-northeast-2.rds.amazonaws.com"
name = "admin"
password = "hdci12#$"
db_name = "ambt"

PORT=3306


conn =  pymysql.connect(host=rds_host_read, user=name, passwd=password, port=PORT, database=db_name, charset='utf8')
#conn = pymysql.connect(host=rds_host, user=name, passwd=password, db=db_name, use_unicode=True, charset='utf8', connect_timeout=5)

sql_statement = "SELECT * FROM `ambt.icos`.facility_type;"
facilityTypeId = pd.read_sql(sql=sql_statement, con=conn)

sql_statement = "SELECT * FROM `ambt.icos`.facility_code;"
facilityCode = pd.read_sql(sql=sql_statement, con=conn)

sql_statement = "SELECT * FROM `ambt.icos`.material_code;"
materialCode = pd.read_sql(sql=sql_statement, con=conn)

sql_statement = "SELECT * FROM `ambt.icos`.control_value;"
controlValue = pd.read_sql(sql=sql_statement, con=conn)

sql_statement = "SELECT * FROM `ambt.icos`.value_type;"
valueType = pd.read_sql(sql=sql_statement, con=conn)

sql_statement = "SELECT * FROM `ambt.icos`.ambt_anoicos_code;"
mappingTable = pd.read_sql(sql=sql_statement, con=conn)


s3_resource = boto3.resource('s3')
bucket = s3_resource.Bucket('hdci-ambt-anoicos-prep')

now = datetime.datetime.now()
updated_date = []
updated_key = []
for bucket_obj in bucket.objects.all():
    calculated_date = bucket_obj.last_modified + datetime.timedelta(hours=9)
    key = bucket_obj.key
    target_year = int(key.split('/')[2].split('=')[-1])
    target_month = int(key.split('/')[3].split('=')[-1])
    target_day = int(key.split('/')[4].split('=')[-1])
    
    appended_data = []
    if now.year == calculated_date.year \
    and now.month == calculated_date.month \
    and now.day == calculated_date.day:
        
        #body = obj.get()['Body'].read()
        processed_data = pd.read_csv(bucket_obj.get()['Body'], sep=',')
        processed_data = processed_data.drop(['Unnamed: 0'], axis=1)
        
        
        ## ----------------------------------------------------------------------------------------------
        ## Service - physics-based anomaly detection for simultaneous valve opening
        
        # facility_type = 1(ahu)
        # facility_code = 4(AHU4_2F)
        # facility_code = 5(AHU6_3F)
        # facility_code = 6(AHU6_4F)
        # facility_code = 7(AHU6_5F)
        # facility_code = 8(AHU6_6F)
        # facility_code = 9(AHU6_7F)
        # facility_code = 10(AHU6_8F)
        # facility_code = 11(AHU6_9F)
        f_c_ahu4_2F = 4
        f_c_ahu6_3F = 5
        f_c_ahu6_4F = 6
        f_c_ahu6_5F = 7
        f_c_ahu6_6F = 8
        f_c_ahu6_7F = 9
        f_c_ahu6_8F = 10
        f_c_ahu6_9F = 11
        AHU4_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) & \
                                    (mappingTable['facility_code'] == f_c_ahu4_2F)]
        AHU3F_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) & \
                                     (mappingTable['facility_code'] == f_c_ahu6_3F)]
        AHU4F_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) & \
                                     (mappingTable['facility_code'] == f_c_ahu6_4F)]
        AHU5F_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) & \
                                     (mappingTable['facility_code'] == f_c_ahu6_5F)]
        AHU6F_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) & \
                                     (mappingTable['facility_code'] == f_c_ahu6_6F)]
        AHU7F_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) & \
                                     (mappingTable['facility_code'] == f_c_ahu6_7F)]
        AHU8F_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) & \
                                     (mappingTable['facility_code'] == f_c_ahu6_8F)]
        AHU9F_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) & \
                                     (mappingTable['facility_code'] == f_c_ahu6_9F)]
        
        # facility_type = 19(밸브)
        # control_value = 7(개도율)
        # material_code = 10(냉수)
        # material_code = 11(온수)
        c_v_open_ratio = 7
        m_c_cool_water = 10
        m_c_hot_water = 11
        
        ahu4_cool_open_ratio_tag = AHU4_row.loc[(AHU4_row['control_value']==c_v_open_ratio) & \
                                                 (AHU4_row['material_code']==m_c_cool_water)]['raw_tag'].values
        ahu4_hot_open_ratio_tag = AHU4_row.loc[(AHU4_row['control_value']==c_v_open_ratio) & \
                                                 (AHU4_row['material_code']==m_c_hot_water)]['raw_tag'].values
        
        ahu3F_name = facilityCode.loc[(facilityCode['facility_code']==f_c_ahu6_3F)]['facility_code_name']
        ahu3F_cool_open_ratio_tag = AHU3F_row.loc[(AHU3F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU3F_row['material_code']==m_c_cool_water)]['raw_tag'].values
        ahu3F_hot_open_ratio_tag = AHU3F_row.loc[(AHU3F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU3F_row['material_code']==m_c_hot_water)]['raw_tag'].values
        
        ahu4F_name = facilityCode.loc[(facilityCode['facility_code']==f_c_ahu6_4F)]['facility_code_name']
        ahu4F_cool_open_ratio_tag = AHU4F_row.loc[(AHU4F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU4F_row['material_code']==m_c_cool_water)]['raw_tag'].values
        ahu4F_hot_open_ratio_tag = AHU4F_row.loc[(AHU4F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU4F_row['material_code']==m_c_hot_water)]['raw_tag'].values
        
        ahu5F_name = facilityCode.loc[(facilityCode['facility_code']==f_c_ahu6_5F)]['facility_code_name']
        ahu5F_cool_open_ratio_tag = AHU5F_row.loc[(AHU5F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU5F_row['material_code']==m_c_cool_water)]['raw_tag'].values
        ahu5F_hot_open_ratio_tag = AHU5F_row.loc[(AHU5F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU5F_row['material_code']==m_c_hot_water)]['raw_tag'].values
        
        ahu6F_name = facilityCode.loc[(facilityCode['facility_code']==f_c_ahu6_6F)]['facility_code_name']
        ahu6F_cool_open_ratio_tag = AHU6F_row.loc[(AHU6F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU6F_row['material_code']==m_c_cool_water)]['raw_tag'].values
        ahu6F_hot_open_ratio_tag = AHU6F_row.loc[(AHU6F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU6F_row['material_code']==m_c_hot_water)]['raw_tag'].values
        
        ahu7F_name = facilityCode.loc[(facilityCode['facility_code']==f_c_ahu6_7F)]['facility_code_name']
        ahu7F_cool_open_ratio_tag = AHU7F_row.loc[(AHU7F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU7F_row['material_code']==m_c_cool_water)]['raw_tag'].values
        ahu7F_hot_open_ratio_tag = AHU7F_row.loc[(AHU7F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU7F_row['material_code']==m_c_hot_water)]['raw_tag'].values
        
        ahu8F_name = facilityCode.loc[(facilityCode['facility_code']==f_c_ahu6_8F)]['facility_code_name']
        ahu8F_cool_open_ratio_tag = AHU8F_row.loc[(AHU8F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU8F_row['material_code']==m_c_cool_water)]['raw_tag'].values
        ahu8F_hot_open_ratio_tag = AHU8F_row.loc[(AHU8F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU8F_row['material_code']==m_c_hot_water)]['raw_tag'].values
        
        ahu9F_name = facilityCode.loc[(facilityCode['facility_code']==f_c_ahu6_9F)]['facility_code_name']
        ahu9F_cool_open_ratio_tag = AHU9F_row.loc[(AHU9F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU9F_row['material_code']==m_c_cool_water)]['raw_tag'].values
        ahu9F_hot_open_ratio_tag = AHU9F_row.loc[(AHU9F_row['control_value']==c_v_open_ratio) & \
                                                 (AHU9F_row['material_code']==m_c_hot_water)]['raw_tag'].values
        

        cool_valve_tag_list = [ahu4_cool_open_ratio_tag, ahu3F_cool_open_ratio_tag, ahu4F_cool_open_ratio_tag, \
                              ahu5F_cool_open_ratio_tag, ahu6F_cool_open_ratio_tag, ahu7F_cool_open_ratio_tag, \
                              ahu8F_cool_open_ratio_tag, ahu9F_cool_open_ratio_tag]
        hot_valve_tag_list = [ahu4_hot_open_ratio_tag, ahu3F_hot_open_ratio_tag, ahu4F_hot_open_ratio_tag, \
                             ahu5F_hot_open_ratio_tag, ahu6F_hot_open_ratio_tag, ahu7F_hot_open_ratio_tag, \
                             ahu8F_hot_open_ratio_tag, ahu9F_hot_open_ratio_tag]
        if target_month >= 6 or target_month <= 9:
            cooling = True
        elif target_month <= 3 or target_month == 12:
            cooling = False
        else:
            for list_i in range(len(cool_valve_tag_list)):

                if sum(processed_data[cool_valve_tag_list[list_i]].values.flatten()) > 0:
                    cooling = True
                    break
                else:
                    cooling = False
            
        for list_i in range(len(cool_valve_tag_list)):

            cool_valve_ = processed_data[cool_valve_tag_list[list_i]].values.flatten()
            hot_valve_ = processed_data[hot_valve_tag_list[list_i]].values.flatten()
            
            anormal_event = 0
            for i in range(len(cool_valve_)):
                
                if cooling == False and (cool_valve_[i] > 0 and hot_valve_[i] > 0):
                    anormal_event = 1
                    detect_code = 4    # simultaneous opening
                    description = "The heating and cooling valves were simultaneously opened in heating period."
                elif cooling == True and hot_valve_[i] > 0:
                    anormal_event = 0
                    detect_code = 1    # simultaneous opening
                    description = "Both valves are used in cooling period."
                else:
                    anormal_event = 0
                    detect_code = 1    # normal
                    description = "Data is not wrong."

                time = datetime.datetime.strptime(processed_data['time'][i], '%Y/%m/%d %H:%M:%S')
                time = str(time).replace('/', '-')
                facility_type_id = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(cool_valve_tag_list[list_i])[0]]['facility_type_id'].values[0]
                facility_code = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(cool_valve_tag_list[list_i])[0]]['facility_code'].values[0]

                material_code_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(cool_valve_tag_list[list_i])[0]]['material_code'].values[0]
                control_value_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(cool_valve_tag_list[list_i])[0]]['control_value'].values[0]
                point_counts_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(cool_valve_tag_list[list_i])[0]]['point_count'].values[0]
                data = [time, facility_type_id, facility_code, anormal_event, detect_code, description, \
                       material_code_, control_value_, point_counts_, cool_valve_[i]]
                appended_data.append(data)

                material_code_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(hot_valve_tag_list[list_i])[0]]['material_code'].values[0]
                control_value_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(hot_valve_tag_list[list_i])[0]]['control_value'].values[0]  
                point_counts_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(hot_valve_tag_list[list_i])[0]]['point_count'].values[0]              
                data = [time, facility_type_id, facility_code, anormal_event, detect_code, description, \
                       material_code_, control_value_, point_counts_, hot_valve_[i]]
                appended_data.append(data)

            data_columns = ['time', 'facility_type_id', 'facility_code', 'anormal_event', 'detect_code', \
                            'description', 'material_code', 'control_value', 'point_count', 'meausred_value']
            df=pd.DataFrame(data=appended_data) 
            df.columns=data_columns
            
            
        ## ----------------------------------------------------------------------------------------------
        ## Service - physics-based anomaly detection for inlet/outlet temperature 

        # FacilityType = 9(냉온수기)
        # FacilityCode = 18(냉온수기1-1)
        # FacilityCode = 19(냉온수기1-2)
        # FacilityCode = 20(냉온수기2)
        # ControlValue = 3(온도)
        CH_1_1_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) \
                                      & (mappingTable['facility_type_id'] == 9) \
                                      & (mappingTable['facility_code'] == 18)]
        CH_1_2_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) \
                                      & (mappingTable['facility_type_id'] == 9) \
                                      & (mappingTable['facility_code'] == 19)]
        CH_2_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) \
                                    & (mappingTable['facility_type_id'] == 9) \
                                    & (mappingTable['facility_code'] == 20)]

        
        # control_value = 1(운전상태)
        # control_value = 3(온도)
        # MaterialCode = 6(급수)
        # MaterialCode = 7(환수)
        c_v_status = 1
        c_v_temperature = 3
        m_c_supply_water = 6
        m_c_return_water = 7
        CH_1_1_name = facilityCode.loc[(facilityCode['facility_code'] == \
                                        CH_1_1_row['facility_code'].values[0])]['facility_code_name']
        CH_1_1_status_tag = CH_1_1_row.loc[(CH_1_1_row['control_value'] == \
                                            c_v_status).values]['raw_tag'].values
        CH_1_1_supply_water_tag = CH_1_1_row.loc[(CH_1_1_row['material_code'] == \
                                                  m_c_supply_water).values]['raw_tag'].values
        CH_1_1_return_water_tag = CH_1_1_row.loc[(CH_1_1_row['material_code'] == \
                                                  m_c_return_water).values]['raw_tag'].values

        CH_1_2_name = facilityCode.loc[(facilityCode['facility_code'] == \
                                        CH_1_2_row['facility_code'].values[0])]['facility_code_name']
        CH_1_2_status_tag = CH_1_2_row.loc[(CH_1_2_row['control_value'] == \
                                            c_v_status).values]['raw_tag'].values
        CH_1_2_supply_water_tag = CH_1_2_row.loc[(CH_1_2_row['material_code'] == \
                                                  m_c_supply_water).values]['raw_tag'].values
        CH_1_2_return_water_tag = CH_1_2_row.loc[(CH_1_2_row['material_code'] == \
                                                  m_c_return_water).values]['raw_tag'].values

        CH_2_name = facilityCode.loc[(facilityCode['facility_code'] == \
                                      CH_2_row['facility_code'].values[0])]['facility_code_name']
        CH_2_status_tag = CH_2_row.loc[(CH_2_row['control_value'] == \
                                        c_v_status).values]['raw_tag'].values
        CH_2_supply_water_tag = CH_2_row.loc[(CH_2_row['material_code'] == \
                                              m_c_supply_water).values]['raw_tag'].values
        CH_2_return_water_tag = CH_2_row.loc[(CH_2_row['material_code'] == \
                                              m_c_return_water).values]['raw_tag'].values


        # FacilityType = 5(냉각탑)
        # FacilityCode = 21(냉각탑1-1)
        # FacilityCode = 22(냉각탑1-2)
        # ControlValue = 3(온도)
        CT_1_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) & \
                                    (mappingTable['facility_type_id'] == 5) & \
                                    (mappingTable['facility_code'] == 21)]
        CT_2_row = mappingTable.loc[(mappingTable['site_id'] == 1) & (mappingTable['collect_status'] == 1) & \
                                    (mappingTable['facility_type_id'] == 5) & \
                                    (mappingTable['facility_code'] == 22)]
        
        CT_1_name = facilityCode.loc[(facilityCode['facility_code'] == \
                                      CT_1_row['facility_code'].values[0])]['facility_code_name']
        CT_1_status_tag = CT_1_row.loc[(CT_1_row['control_value'] == \
                                        c_v_status).values]['raw_tag'].values
        CT_1_supply_water_tag = CT_1_row.loc[(CT_1_row['material_code'] == \
                                              m_c_supply_water).values]['raw_tag'].values
        CT_1_return_water_tag = CT_1_row.loc[(CT_1_row['material_code'] == \
                                              m_c_return_water).values]['raw_tag'].values

        CT_2_name = facilityCode.loc[(facilityCode['facility_code'] == \
                                      CT_2_row['facility_code'].values[0])]['facility_code_name']
        CT_2_status_tag = CT_2_row.loc[(CT_2_row['control_value'] == \
                                        c_v_status).values]['raw_tag'].values
        CT_2_supply_water_tag = CT_2_row.loc[(CT_2_row['material_code'] == \
                                              m_c_supply_water).values]['raw_tag'].values
        CT_2_return_water_tag = CT_2_row.loc[(CT_2_row['material_code'] == \
                                              m_c_return_water).values]['raw_tag'].values

        
        name_list = [CH_1_1_name, CH_1_2_name, CH_2_name]
        status_tag_list = [CH_1_1_status_tag, CH_1_2_status_tag, CH_2_status_tag]
        supply_water_tag_list = [CH_1_1_supply_water_tag, CH_1_2_supply_water_tag, CH_2_supply_water_tag]
        return_water_tag_list = [CH_1_1_return_water_tag, CH_1_2_return_water_tag, CH_2_return_water_tag]
        
        for list_i in range(len(name_list)):
            
            status_ = processed_data[status_tag_list[list_i]].values.sum(axis=1)
            supply_water_ = processed_data[supply_water_tag_list[list_i]].values.flatten()
            return_water_ = processed_data[return_water_tag_list[list_i]].values.flatten()

            init_on_cnt = 0
            anormal_event = 0
            for i in range(len(status_)):   
                if status_[i] == 1:
                    init_on_cnt += 1
                    if init_on_cnt < 5:
                        anormal_event = 0
                        detect_code = 1    # normal
                        description = "It has been less than an hour since the equipment was put into operation."                        
                    elif cooling == False and supply_water_[i] < return_water_[i]: 
                        anormal_event = 1
                        detect_code = 2    # supply < return temp. -> wrong
                        description = "supply temperature of heater is not higer than return."
                    elif cooling == True and supply_water_[i] > return_water_[i]: 
                        anormal_event = 1
                        detect_code = 2    # supply < return temp. -> wrong
                        description = "supply temperature of chiller is not lower than return."
                    else:
                        anormal_event = 0
                        detect_code = 1    # normal
                        description = "Data is not wrong."
                else:
                    anormal_event = 0
                    detect_code = 1    # normal
                    description = "Data is not wrong."
                    
                        
                time = datetime.datetime.strptime(processed_data['time'][i], '%Y/%m/%d %H:%M:%S')
                time = str(time).replace('/', '-')
                facility_type_id = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(status_tag_list[list_i])[0]]['facility_type_id'].values[0]
                facility_code = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(status_tag_list[list_i])[0]]['facility_code'].values[0]

                material_code_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(status_tag_list[0])[0]]['material_code'].values[0]
                control_value_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(status_tag_list[0])[0]]['control_value'].values[0]
                point_counts_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(status_tag_list[0])[0]]['point_count'].values[0]
                data = [time, facility_type_id, facility_code, anormal_event, detect_code, description, \
                       material_code_, control_value_, point_counts_, status_[i]]
                appended_data.append(data)

                material_code_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(supply_water_tag_list[0])[0]]['material_code'].values[0]
                control_value_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(supply_water_tag_list[0])[0]]['control_value'].values[0]  
                point_counts_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(supply_water_tag_list[0])[0]]['point_count'].values[0]              
                data = [time, facility_type_id, facility_code, anormal_event, detect_code, description, \
                       material_code_, control_value_, point_counts_, supply_water_[i]]
                appended_data.append(data)

                material_code_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(return_water_tag_list[0])[0]]['material_code'].values[0]
                control_value_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(return_water_tag_list[0])[0]]['control_value'].values[0]   
                point_counts_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(return_water_tag_list[0])[0]]['point_count'].values[0]              
                data = [time, facility_type_id, facility_code, anormal_event, detect_code, description, \
                       material_code_, control_value_, point_counts_, return_water_[i]]
                appended_data.append(data)

            data_columns = ['time', 'facility_type_id', 'facility_code', 'anormal_event', 'detect_code', \
                            'description', 'material_code', 'control_value', 'point_count', 'meausred_value']
            df=pd.DataFrame(data=appended_data) 
            df.columns=data_columns
            
            
        ## ----------------------------------------------------------------------------------------------
        ## Service - physics-based anomaly detection for set point
        
        # control_value = 1(운전상태)
        # control_value = 3(온도)
        # control_value = 5(온도 설정값)
        # material_code = 4(환기)
        # facility_type_id = 1(공조기)
        # facility_type_id = 6(팬)
        f_t_ahu = 1
        f_t_fan = 6
        c_v_status = 1
        c_v_temperature = 3
        c_v_temperature_SP = 5
        m_c_RA = 4
        
        ahu4_RF_status_tag = AHU4_row.loc[(AHU4_row['facility_type_id']==f_t_fan) & \
                                          (AHU4_row['control_value']==c_v_status) & \
                                          (AHU4_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu4_RA_tag = AHU4_row.loc[(AHU4_row['control_value']==c_v_temperature) & \
                                   (AHU4_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu4_SP_tag = AHU4_row.loc[(AHU4_row['control_value']==c_v_temperature_SP) & \
                                   (AHU4_row['material_code']==m_c_RA)]['raw_tag'].values
        
        
        ahu3F_RF_status_tag = AHU3F_row.loc[(AHU3F_row['facility_type_id']==f_t_fan) & \
                                            (AHU3F_row['control_value']==c_v_status) & \
                                            (AHU3F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu3F_RA_tag = AHU3F_row.loc[(AHU3F_row['control_value']==c_v_temperature) & \
                                     (AHU3F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu3F_SP_tag = AHU3F_row.loc[(AHU3F_row['control_value']==c_v_temperature_SP) & \
                                     (AHU3F_row['material_code']==m_c_RA)]['raw_tag'].values
        
        ahu4F_RF_status_tag = AHU4F_row.loc[(AHU4F_row['facility_type_id']==f_t_fan) & \
                                            (AHU4F_row['control_value']==c_v_status) & \
                                            (AHU4F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu4F_RA_tag = AHU4F_row.loc[(AHU4F_row['control_value']==c_v_temperature) & \
                                     (AHU4F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu4F_SP_tag = AHU4F_row.loc[(AHU4F_row['control_value']==c_v_temperature_SP) & \
                                     (AHU4F_row['material_code']==m_c_RA)]['raw_tag'].values
        
        ahu5F_RF_status_tag = AHU5F_row.loc[(AHU5F_row['facility_type_id']==f_t_fan) & \
                                            (AHU5F_row['control_value']==c_v_status) & \
                                            (AHU5F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu5F_RA_tag = AHU5F_row.loc[(AHU5F_row['control_value']==c_v_temperature) & \
                                     (AHU5F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu5F_SP_tag = AHU5F_row.loc[(AHU5F_row['control_value']==c_v_temperature_SP) & \
                                   (AHU5F_row['material_code']==m_c_RA)]['raw_tag'].values
        
        ahu6F_RF_status_tag = AHU6F_row.loc[(AHU6F_row['facility_type_id']==f_t_fan) & \
                                            (AHU6F_row['control_value']==c_v_status) & \
                                            (AHU6F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu6F_RA_tag = AHU6F_row.loc[(AHU6F_row['control_value']==c_v_temperature) & \
                                     (AHU6F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu6F_SP_tag = AHU6F_row.loc[(AHU6F_row['control_value']==c_v_temperature_SP) & \
                                     (AHU6F_row['material_code']==m_c_RA)]['raw_tag'].values
        
        ahu7F_RF_status_tag = AHU7F_row.loc[(AHU7F_row['facility_type_id']==f_t_fan) & \
                                            (AHU7F_row['control_value']==c_v_status) & \
                                            (AHU7F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu7F_RA_tag = AHU7F_row.loc[(AHU7F_row['control_value']==c_v_temperature) & \
                                     (AHU7F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu7F_SP_tag = AHU7F_row.loc[(AHU7F_row['control_value']==c_v_temperature_SP) & \
                                     (AHU7F_row['material_code']==m_c_RA)]['raw_tag'].values
        
        ahu8F_RF_status_tag = AHU8F_row.loc[(AHU8F_row['facility_type_id']==f_t_fan) & \
                                            (AHU8F_row['control_value']==c_v_status) & \
                                            (AHU8F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu8F_RA_tag = AHU8F_row.loc[(AHU8F_row['control_value']==c_v_temperature) & \
                                     (AHU8F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu8F_SP_tag = AHU8F_row.loc[(AHU8F_row['control_value']==c_v_temperature_SP) & \
                                     (AHU8F_row['material_code']==m_c_RA)]['raw_tag'].values
        
        ahu9F_RF_status_tag = AHU9F_row.loc[(AHU9F_row['facility_type_id']==f_t_fan) & \
                                            (AHU9F_row['control_value']==c_v_status) & \
                                            (AHU9F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu9F_RA_tag = AHU9F_row.loc[(AHU9F_row['control_value']==c_v_temperature) & \
                                     (AHU9F_row['material_code']==m_c_RA)]['raw_tag'].values
        ahu9F_SP_tag = AHU9F_row.loc[(AHU9F_row['control_value']==c_v_temperature_SP) & \
                                     (AHU9F_row['material_code']==m_c_RA)]['raw_tag'].values


            
        RF_status_tag_list = [ahu4_RF_status_tag, ahu3F_RF_status_tag, ahu4F_RF_status_tag, ahu5F_RF_status_tag, \
                             ahu6F_RF_status_tag, ahu7F_RF_status_tag, ahu8F_RF_status_tag, ahu9F_RF_status_tag]
        RA_tag_list = [ahu4_RA_tag, ahu3F_RA_tag, ahu4F_RA_tag, ahu5F_RA_tag, ahu6F_RA_tag, \
                      ahu7F_RA_tag, ahu8F_RA_tag, ahu9F_RA_tag]
        RA_SP_tag_list = [ahu4_SP_tag, ahu3F_SP_tag, ahu4F_SP_tag, ahu5F_SP_tag, ahu6F_SP_tag, ahu7F_SP_tag, \
                         ahu8F_SP_tag, ahu9F_SP_tag]

        for list_i in range(len(RF_status_tag_list)):

            RF_status_ = processed_data[RF_status_tag_list[list_i]].values.flatten()
            RA_ = processed_data[RA_tag_list[list_i]].values.flatten()
            RA_SP_ = processed_data[RA_SP_tag_list[list_i]].values.flatten()
            init_on_cnt = 0
            anormal_event = 0
            for i in range(len(RA_)):
                if RF_status_[i] == 1:
                    init_on_cnt += 1
                    if init_on_cnt < 5:
                        anormal_event = 0                        
                        detect_code = 1    # normal
                        description = "It has been less than an hour since the equipment was put into operation."
                    if abs(RA_[i] - RA_SP_[i]) > 5:
                        anormal_event = 1
                        detect_code = 5    # Validation of set points
                        description = \
                        "Data is out of range for the setpoint during equipment operation. (tolerance: abs. 5 Celsius)"
                    else:
                        anormal_event = 0
                        detect_code = 1    # normal
                        description = "Data is not wrong."
                else:
                    anormal_event = 0
                    detect_code = 1    # normal
                    description = "Data is not wrong."
                        
                        
                time = datetime.datetime.strptime(processed_data['time'][i], '%Y/%m/%d %H:%M:%S')
                time = str(time).replace('/', '-')
                facility_code = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RF_status_tag_list[list_i])[0]]['facility_code'].values[0]

                facility_type_id_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RF_status_tag_list[list_i])[0]]['facility_type_id'].values[0]
                material_code_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RF_status_tag_list[0])[0]]['material_code'].values[0]
                control_value_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RF_status_tag_list[0])[0]]['control_value'].values[0]
                point_counts_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RF_status_tag_list[0])[0]]['point_count'].values[0]
                data = [time, facility_type_id_, facility_code, anormal_event, detect_code, description, \
                       material_code_, control_value_, point_counts_, RF_status_[i]]
                appended_data.append(data)

                facility_type_id_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RA_tag_list[list_i])[0]]['facility_type_id'].values[0]
                material_code_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RA_tag_list[0])[0]]['material_code'].values[0]
                control_value_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RA_tag_list[0])[0]]['control_value'].values[0]  
                point_counts_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RA_tag_list[0])[0]]['point_count'].values[0]              
                data = [time, facility_type_id_, facility_code, anormal_event, detect_code, description, \
                       material_code_, control_value_, point_counts_, RA_[i]]
                appended_data.append(data)

                facility_type_id_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RA_SP_tag_list[list_i])[0]]['facility_type_id'].values[0]
                material_code_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RA_SP_tag_list[0])[0]]['material_code'].values[0]
                control_value_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RA_SP_tag_list[0])[0]]['control_value'].values[0]   
                point_counts_ = mappingTable.loc[mappingTable['raw_tag'] == \
                                                 list(RA_SP_tag_list[0])[0]]['point_count'].values[0]              
                data = [time, facility_type_id_, facility_code, anormal_event, detect_code, description, \
                       material_code_, control_value_, point_counts_, RA_SP_[i]]
                appended_data.append(data)

            data_columns = ['time', 'facility_type_id', 'facility_code', 'anormal_event', 'detect_code', \
                            'description', 'material_code', 'control_value', 'point_count', 'meausred_value']
            df=pd.DataFrame(data=appended_data) 
            df.columns=data_columns

            
        
        pred_output_bucket = 'hdci-ambt-anoicos-serv'

        month_str = "0" + str(target_month) if target_month < 10 else target_month
        day_str = "0" + str(target_day) if target_day < 10 else target_day

        s3_db_path="s3://{}/dev/site_name=ipark_tower/year={}/month={}/day={}" \
        .format(pred_output_bucket, target_year, month_str, day_str)  

        res=wr.s3.to_parquet(df=df,path=s3_db_path,dataset=True,mode='overwrite')
        #print(s3_db_path)
